In [1]:
import numpy as np
import time
import pickle
import os
import matplotlib.pyplot as plt
import warnings
import pandas as pd

warnings.filterwarnings('ignore')

In [2]:
print("----------------Reading the Data-------------------------")
PATH = os.getcwd()
os.chdir('Alphabets/')

X_train = pd.read_csv('train.csv', sep=',', header=None, index_col=False)
X_test = pd.read_csv('test.csv', sep=',', header=None, index_col=False)
np.random.shuffle(X_train.to_numpy())
train_class = X_train[X_train.columns[-1]]
test_actual_class = X_test[X_test.columns[-1]]

X_train = X_train.drop(X_train.columns[-1], axis=1)
X_test = X_test.drop(X_test.columns[-1], axis=1)

print("----------------Data Reading completed-------------------")

os.chdir('../')

X_train = X_train/255
X_test = X_test/255

m = X_train.shape[0] # Number of Training Samples

X_valid = X_train.iloc[(int(0.85*m)):]
valid_class = train_class[(int(0.85*m)):]
X_train = X_train.iloc[0:int(0.85*m)]
train_class = train_class[0:int(0.85*m)]


m = X_train.shape[0] # Number of Training Samples
n = X_train.shape[1] # Number of input features

print("The total number of training samples = {}".format(m))
print("The total number of validation samples = {}".format(X_valid.shape[0]))

print("The number of features = {}".format(n))

----------------Reading the Data-------------------------
----------------Data Reading completed-------------------
The total number of training samples = 11050
The total number of validation samples = 1950
The number of features = 784


In [3]:
#To get the one hot encoding of each label
print("--------Perform 1-hot encoding of class labels------------")

train_class_enc = pd.get_dummies(train_class).to_numpy()
valid_class_enc = pd.get_dummies(valid_class).to_numpy()
test_actual_class_enc = pd.get_dummies(test_actual_class).to_numpy()

--------Perform 1-hot encoding of class labels------------


In [4]:
#Add the intercept term to the data samples both in training and test dataset
X_train = np.hstack((np.ones((m,1)),X_train.to_numpy()))
X_valid = np.hstack((np.ones((X_valid.shape[0],1)), X_valid.to_numpy()))
X_test = np.hstack((np.ones((X_test.shape[0],1)),X_test.to_numpy()))

In [31]:
lr = 0.1
arch_test = [1,5,10,50,100]
arch = [arch_test[3]] #means one hidden layer with 2 perceptrons 
batch_size = 100 # Mini-Batch Size
r = np.max(train_class) + 1 # Default value of the number of classes = 26

In [6]:
#Mini-Batch formation
mini_batch = [(X_train[i:i+batch_size,:], train_class_enc[i:i+batch_size]) for i in range(0, m, batch_size)]
print("The number of mini-batches formed is = {}".format(len(mini_batch)))

The number of mini-batches formed is = 111


In [7]:
#Theta Initialization 
def theta_init(arch=[50]):
    theta = []
    for i in range(len(arch)+1):
        if i == 0:
            dim0=n+1
            dim1=arch[i]
        elif (i == len(arch)):
            dim0=arch[i-1]
            dim1 = r
        else:
            dim0=arch[i-1]
            dim1= arch[i]

        theta.append(2*np.random.random((dim0, dim1))-1)
        #theta.append(np.zeros((dim0, dim1)))
    return theta

In [8]:
def activation(x):
    return 1/(1+np.exp(-x))

In [9]:
def forward_prop(data, theta):
    fm = []
    fm.append(data)
    for l in range(len(theta)):
        fm.append(activation(np.dot(fm[l], theta[l])))
    return fm

In [10]:
def cost_total(X, theta, Y, m):
    fm = forward_prop(X, theta)
    cost = (1/(2*m))*np.sum((Y-fm[-1])**2)
    return cost

In [11]:
def calc_accuracy(data, theta, actual_class):
    pred_class = forward_prop(data, theta)
    test_pred_class = pred_class[-1]
    for i in range(len(test_pred_class)):
        test_pred_class[i][test_pred_class[i] == np.max(test_pred_class[i])] = 1
        test_pred_class[i][test_pred_class[i] != np.max(test_pred_class[i])] = 0


    test_acc = 0
    for i in range(len(actual_class)):
        if (np.array_equal(test_pred_class[i], actual_class[i])):
            test_acc+=1
    test_acc /= data.shape[0]

    #print("The Test Accuracy of the model = {}%".format(test_acc*100))
    return (test_acc*100)

In [12]:
epochs = []
train_accuracy = []
test_accuracy = []
valid_accuracy=[]
train_time = []

In [36]:
arch_test = [1, 5, 10, 50, 100]
#arch_test = [50]

In [ ]:
lr0=1.1
for i in range(len(arch_test)):
    theta = theta_init([arch_test[i]])
    fm = forward_prop(X_train, theta)
    epoch = 1
    start = time.time()
    cost_init = cost_total(X_valid, theta, valid_class_enc, m)

    while(True):
        count = 0
        lr = lr0/(np.power(epoch, 1/3))
        print("learning rate = ", lr)

        print("Initial Cost on Val dataset for this epoch {} = {}".format(epoch, cost_init))

        for b in mini_batch:
            X_b = b[0]
            Y_b = b[1]
            fm = forward_prop(X_b, theta)
            delta = [None]*len(fm)

            if (count % 60 == 0):
                print("Error on this batch = "+str(cost_total(X_b, theta, Y_b, batch_size)))
            #Backward Propagation

            for l in range(len(fm)-1, 0, -1):
                if (l == len(fm)-1):
                    delta[l] = ((1/batch_size)*(Y_b - fm[l])*fm[l]*(1-fm[l]))
                else:
                    delta[l]=(np.dot(delta[l+1], theta[l].T)*fm[l]*(1-fm[l]))

            for t in range(len(theta)):
                theta[t] += lr*np.dot(fm[t].T, delta[t+1]) 

            count+=1
        epoch+=1 #Number of epochs
        
        cost_final = cost_total(X_valid, theta, valid_class_enc, m)
        print("Cost on val dataset after {} epochs is = {}".format(epoch, cost_final))
        if (abs(cost_final-cost_init) < 1e-07):
            print("cost initial= {} , cost final={} , change in cost= {}".format(cost_init,cost_final, cost_final-cost_init))
            break
        cost_init = cost_final
    epochs.append(epoch)
    train_time.append(time.time()-start)
    train_accuracy.append(calc_accuracy(X_train, theta, train_class_enc))
    valid_accuracy.append(calc_accuracy(X_valid, theta, valid_class_enc))
    test_accuracy.append(calc_accuracy(X_test, theta, test_actual_class_enc))
    print("\n------------------------------------------------------------------------------")
    print("The stats for number of units in the hidden layer = {} are as below:".format(arch_test[i]))
    print("------------------------------------------------------------------------------")
    print("The number of epochs = {:2.3f}".format(epochs[-1]))
    print("The training time = {:2.3f}sec".format(train_time[-1]))
    print("The training accuracy is = {:2.3f}%".format(train_accuracy[-1]))
    print("The validation accuracy is = {:2.3f}%".format(valid_accuracy[-1]))
    print("The test accuracy is = {:2.3f}%".format(test_accuracy[-1]))
    print("------------------------------------------------------------------------------\n")

learning rate =  1.1
Initial Cost on Val dataset for this epoch 1 = 0.5683113833589193
Error on this batch = 3.226044222472448
Error on this batch = 0.5732701020932426
Cost on val dataset after 2 epochs is = 0.0909571966947729
learning rate =  0.8730705785825098
Initial Cost on Val dataset for this epoch 2 = 0.0909571966947729
Error on this batch = 0.5155342648851285
Error on this batch = 0.49965753832222093
Cost on val dataset after 3 epochs is = 0.08706911446751914
learning rate =  0.7626974017856982
Initial Cost on Val dataset for this epoch 3 = 0.08706911446751914
Error on this batch = 0.4933953339190393
Error on this batch = 0.48956440414473323
Cost on val dataset after 4 epochs is = 0.08603630300694488
learning rate =  0.6929565774421803
Initial Cost on Val dataset for this epoch 4 = 0.08603630300694488
Error on this batch = 0.4875247082514087
Error on this batch = 0.4859285896317475
Cost on val dataset after 5 epochs is = 0.0855919654705488
learning rate =  0.6432839024068306
In

Cost on val dataset after 37 epochs is = 0.08485522490016903
learning rate =  0.330110073390418
Initial Cost on Val dataset for this epoch 37 = 0.08485522490016903
Error on this batch = 0.4807820925116769
Error on this batch = 0.48073511909171934
Cost on val dataset after 38 epochs is = 0.08485492416531655
learning rate =  0.32718859209245166
Initial Cost on Val dataset for this epoch 38 = 0.08485492416531655
Error on this batch = 0.4807799676902407
Error on this batch = 0.48073296566807044
Cost on val dataset after 39 epochs is = 0.08485466036444521
learning rate =  0.32436786041931415
Initial Cost on Val dataset for this epoch 39 = 0.08485466036444521
Error on this batch = 0.48077806790384764
Error on this batch = 0.48073102740940443
Cost on val dataset after 40 epochs is = 0.08485442884215952
learning rate =  0.3216419512034153
Initial Cost on Val dataset for this epoch 40 = 0.08485442884215952
Error on this batch = 0.48077636601219026
Error on this batch = 0.4807292790420203
Cost o

Cost on val dataset after 25 epochs is = 0.08485248585035796
learning rate =  0.37619470826887336
Initial Cost on Val dataset for this epoch 25 = 0.08485248585035796
Error on this batch = 0.4807175487952136
Error on this batch = 0.48099942188140743
Cost on val dataset after 26 epochs is = 0.08485040878509684
learning rate =  0.37130850964854006
Initial Cost on Val dataset for this epoch 26 = 0.08485040878509684
Error on this batch = 0.4807116235621941
Error on this batch = 0.48101390058014776
Cost on val dataset after 27 epochs is = 0.08484821846451437
learning rate =  0.3666666666666667
Initial Cost on Val dataset for this epoch 27 = 0.08484821846451437
Error on this batch = 0.4807048105715082
Error on this batch = 0.48103020073422464
Cost on val dataset after 28 epochs is = 0.08484588425501415
learning rate =  0.3622485658045923
Initial Cost on Val dataset for this epoch 28 = 0.08484588425501415
Error on this batch = 0.48069691757420585
Error on this batch = 0.48104855181638867
Cost 

Cost on val dataset after 60 epochs is = 0.0843447319967859
learning rate =  0.2809801252109695
Initial Cost on Val dataset for this epoch 60 = 0.0843447319967859
Error on this batch = 0.4762196341761865
Error on this batch = 0.4805806910503544
Cost on val dataset after 61 epochs is = 0.08432547093782633
learning rate =  0.27943624721030297
Initial Cost on Val dataset for this epoch 61 = 0.08432547093782633
Error on this batch = 0.47604725243162327
Error on this batch = 0.4804904186973829
Cost on val dataset after 62 epochs is = 0.08430647367146947
learning rate =  0.27792575150607113
Initial Cost on Val dataset for this epoch 62 = 0.08430647367146947
Error on this batch = 0.4758805305904645
Error on this batch = 0.48040016536168173
Cost on val dataset after 63 epochs is = 0.0842877138820704
learning rate =  0.2764473950806898
Initial Cost on Val dataset for this epoch 63 = 0.0842877138820704
Error on this batch = 0.4757186265743086
Error on this batch = 0.48031039527488617
Cost on val

Cost on val dataset after 95 epochs is = 0.0837779540108929
learning rate =  0.24107461585287857
Initial Cost on Val dataset for this epoch 95 = 0.0837779540108929
Error on this batch = 0.4717911488293585
Error on this batch = 0.47800556075702816
Cost on val dataset after 96 epochs is = 0.08376468443365594
learning rate =  0.2402346278024822
Initial Cost on Val dataset for this epoch 96 = 0.08376468443365594
Error on this batch = 0.47169428939514796
Error on this batch = 0.47794132187740834
Cost on val dataset after 97 epochs is = 0.08375156629988632
learning rate =  0.2394062259560102
Initial Cost on Val dataset for this epoch 97 = 0.08375156629988632
Error on this batch = 0.4715984982339472
Error on this batch = 0.4778771516906899
Cost on val dataset after 98 epochs is = 0.08373859798574436
learning rate =  0.2385891335045164
Initial Cost on Val dataset for this epoch 98 = 0.08373859798574436
Error on this batch = 0.47150374365302455
Error on this batch = 0.47781306304507115
Cost on 

...

Error on this batch = 0.36488652134105837
Cost on val dataset after 19299 epochs is = 0.0685601865368362
learning rate =  0.041009179781797134
Initial Cost on Val dataset for this epoch 19299 = 0.0685601865368362
Error on this batch = 0.3678419736602854
Error on this batch = 0.36488451010055417
Cost on val dataset after 19300 epochs is = 0.06855989795055452
learning rate =  0.04100847149357471
Initial Cost on Val dataset for this epoch 19300 = 0.06855989795055452
Error on this batch = 0.3678416021202388
Error on this batch = 0.3648824989749797
Cost on val dataset after 19301 epochs is = 0.06855960933302152
learning rate =  0.041007763254282424
Initial Cost on Val dataset for this epoch 19301 = 0.06855960933302152
Error on this batch = 0.3678412302254019
Error on this batch = 0.3648804879662821
Cost on val dataset after 19302 epochs is = 0.06855932068420838
learning rate =  0.04100705506391437
Initial Cost on Val dataset for this epoch 19302 = 0.06855932068420838
Error on this batch = 0

Error on this batch = 0.36481821547688437
Cost on val dataset after 19333 epochs is = 0.06855035690641428
learning rate =  0.04098512539669427
Initial Cost on Val dataset for this epoch 19333 = 0.06855035690641428
Error on this batch = 0.36782914452363513
Error on this batch = 0.3648162092601319
Cost on val dataset after 19334 epochs is = 0.06855006724240822
learning rate =  0.04098441876878433
Initial Cost on Val dataset for this epoch 19334 = 0.06855006724240822
Error on this batch = 0.3678287611356366
Error on this batch = 0.36481420322671476
Cost on val dataset after 19335 epochs is = 0.06854977754626472
learning rate =  0.04098371218960398
Initial Cost on Val dataset for this epoch 19335 = 0.06854977754626472
Error on this batch = 0.36782837740619606
Error on this batch = 0.3648121973787097
Cost on val dataset after 19336 epochs is = 0.06854948781796076
learning rate =  0.04098300565914735
Initial Cost on Val dataset for this epoch 19336 = 0.06854948781796076
Error on this batch =

Error on this batch = 0.36475011954035724
Cost on val dataset after 19367 epochs is = 0.06854049017204118
learning rate =  0.04096112734991928
Initial Cost on Val dataset for this epoch 19367 = 0.06854049017204118
Error on this batch = 0.3678159203279737
Error on this batch = 0.36474812074169977
Cost on val dataset after 19368 epochs is = 0.06854019940357305
learning rate =  0.04096042237552281
Initial Cost on Val dataset for this epoch 19368 = 0.06854019940357305
Error on this batch = 0.3678155255707863
Error on this batch = 0.36474612219877955
Cost on val dataset after 19369 epochs is = 0.06853990860229102
learning rate =  0.04095971744965657
Initial Cost on Val dataset for this epoch 19369 = 0.06853990860229102
Error on this batch = 0.367815130486819
Error on this batch = 0.36474412391377614
Cost on val dataset after 19370 epochs is = 0.06853961776817864
learning rate =  0.04095901257231472
Initial Cost on Val dataset for this epoch 19370 = 0.06853961776817864
Error on this batch = 

Error on this batch = 0.3646823170025248
Cost on val dataset after 19401 epochs is = 0.0685305855464997
learning rate =  0.04093718541096226
Initial Cost on Val dataset for this epoch 19401 = 0.0685305855464997
Error on this batch = 0.3678023178834715
Error on this batch = 0.3646803281348952
Cost on val dataset after 19402 epochs is = 0.06853029365435397
learning rate =  0.04093648208331997
Initial Cost on Val dataset for this epoch 19402 = 0.06853029365435397
Error on this batch = 0.36780191226121156
Error on this batch = 0.3646783395982878
Cost on val dataset after 19403 epochs is = 0.06853000172895093
learning rate =  0.04093577880400972
Initial Cost on Val dataset for this epoch 19403 = 0.06853000172895093
Error on this batch = 0.3678015063269638
Error on this batch = 0.36467635139494625
Cost on val dataset after 19404 epochs is = 0.06852970977028129
learning rate =  0.04093507557302568
Initial Cost on Val dataset for this epoch 19404 = 0.06852970977028129
Error on this batch = 0.3

Error on this batch = 0.36461489467488817
Cost on val dataset after 19435 epochs is = 0.068520642510805
learning rate =  0.04091329935065831
Initial Cost on Val dataset for this epoch 19435 = 0.068520642510805
Error on this batch = 0.36778835418590883
Error on this batch = 0.36461291832571235
Cost on val dataset after 19436 epochs is = 0.06852034948402154
learning rate =  0.040912597663050325
Initial Cost on Val dataset for this epoch 19436 = 0.06852034948402154
Error on this batch = 0.3677879381867013
Error on this batch = 0.3646109423842405
Cost on val dataset after 19437 epochs is = 0.06852005642378968
learning rate =  0.04091189602357732
Initial Cost on Val dataset for this epoch 19437 = 0.06852005642378968
Error on this batch = 0.36778752188918545
Error on this batch = 0.36460896685273114
Cost on val dataset after 19438 epochs is = 0.0685197633301078
learning rate =  0.040911194432233504
Initial Cost on Val dataset for this epoch 19438 = 0.0685197633301078
Error on this batch = 0.

In [42]:
test_accuracy

[3.8461538461538463,
 14.046153846153848,
 68.27692307692308,
 86.01538461538462,
 80.07692307692308,
 77.04615384615384,
 80.87692307692308,
 79.93846153846154,
 3.8461538461538463,
 3.8461538461538463,
 20.200000000000003,
 69.15384615384616,
 84.96923076923078,
 84.43076923076923]

In [43]:
epochs

[52,
 4437,
 9803,
 7909,
 14918,
 9888,
 10596,
 6803,
 145,
 180,
 2414,
 1578,
 3823,
 2796]

In [44]:
valid_accuracy


[3.128205128205128,
 14.000000000000002,
 69.94871794871796,
 86.56410256410257,
 80.35897435897435,
 77.64102564102564,
 81.8974358974359,
 80.82051282051282,
 3.897435897435898,
 3.128205128205128,
 19.692307692307693,
 69.28205128205128,
 87.02564102564102,
 84.1025641025641]

In [40]:
1.5/np.power(2039, (1/3))

0.118291130898163